In [13]:
import os
import json
import numpy as np
import requests
from pathlib import Path
from sentence_transformers import SentenceTransformer
from typing import List, Dict, Tuple
import time
from ollama import Client
from IPython.display import Audio
from kokoro import KPipeline
import soundfile as sf
# Configuration


In [14]:
from qdrant_client import QdrantClient

client = QdrantClient(host="localhost", port=6333)

# Example: get collections
print(client.get_collections())

collections=[CollectionDescription(name='buddhist_texts_mn')]


In [15]:
EMBEDDING_MODEL = "all-MiniLM-L6-v2"
embedding_model = SentenceTransformer(EMBEDDING_MODEL)

In [16]:
query= "give me a guided breath meditation step by step based on the anapanasati and the satipatana suttas that would lead me to insight"
query_embedding = embedding_model.encode(query).tolist()

In [17]:
results = client.search(
    collection_name="buddhist_texts_mn",
    query_vector=query_embedding,
    limit=50,
    with_payload=True   # top 5 most similar
)

/tmp/ipykernel_5506/494948396.py:1: DeprecationWarning: `search` method is deprecated and will be removed in the future. Use `query_points` instead.
  results = client.search(


In [18]:
context = "\n\n".join([r.payload.get("text", "") for r in results])


In [65]:
context

'meditation [2] of mindfulness of in-&-out breathing The meditation of mindfulness of in-&-out breathing, when developed & pursued, is of great fruit, of great benefit " Then Ven Rahula, emerging from his seclusion in the late afternoon, went to the Blessed One and, having bowed down, sat to one side As he was sitting there he said to him, "How, lord, is mindfulness of in-&-out breathing to be developed & pursued so as to be of great fruit, of great benefit\n\nEnlightenment-factor of mindfulness: sati sambojjhaṅga 34 Detachment: viveka 35 Freedom from attachment: virāga 36 Cessation: nirodha 37 vossagga 38 dhammavicaya sambojjhaṅga 39 vīriya sambojjhaṅga 40 pīti sambojjhaṅga 41 passaddhi sambojjhaṅga 42 samādhi sambojjhaṅga 43 upekkhā sambojjhaṅga 44 The most crucial point in ¶27 is the practice of the four Satipaṭṭhānas It is the one and only way for the attainment of maggas and phalas and also for the realization of Nibbāna\n\nis how mindfulness of in-&-out breathing is developed & p

In [26]:
prompt = f"""
Eres un guía de meditación con profundo conocimiento de las enseñanzas budistas.

Usa el siguiente contexto (en inglés) como fuente de inspiración para crear una guía de meditación paso a paso.

Escríbela completamente en **español**, usando un tono **calmado, contemplativo, suave y claro**. Evita traducir literalmente el contexto. No lo menciones directamente.

Escribe la guía como si fuera a ser narrada en audio durante aproximadamente **dos minutos**.

Divide el texto en **secciones cortas**, cada una con una **pausa sugerida al final** (por ejemplo: “[pausa]”, “[silencio]”, o “[respira profundamente]”).

Haz frases breves y utiliza silencios sugeridos, respiraciones conscientes y un ritmo pausado.

La estructura debe permitir que el oyente escuche con calma, respire con conciencia y se relaje gradualmente. El objetivo es una experiencia clara, pausada y meditativa.

### Contexto (en inglés):
{context}

### Guía en español:
"""


In [27]:
ollama_client = Client(host='http://localhost:11434')  # Default port

In [28]:
response = ollama_client.chat(
    model="mistral",  # or "llama3", etc.
    messages=[
        {"role": "user", "content": prompt}
    ]
)

In [29]:
print(response['message']['content'])

 La meditación de la respiración es una forma de práctica que se centra en el reconocimiento y la observación del proceso natural de respirar. La persona que practica esta meditación se sienta cómodamente, coloca sus piernas cruzadas y mantiene su cuerpo recto. Después, centra su atención en el acto de respirar, sin intentar modificarlo ni controlarlo de alguna manera.

En esta práctica se recomienda tener en mente los siguientes puntos:

* Sienta cómodamente y coloca sus piernas cruzadas
* Mantiene su cuerpo recto y su espalda derecha
* Centra su atención en el acto de respirar
* No intenta modificar o controlar la respiración

Es importante tener en mente que la práctica de la meditación de la respiración no tiene por objetivo conseguir un resultado específico. Su finalidad es centrar y calmar la mente, así como ayudar a desarrollar una mayor conciencia y comprensión del propio cuerpo y la respiración.

En la tradición budista, la meditación de la respiración se considera una forma e

In [40]:
pipeline = KPipeline(lang_code='e')

# Texto de ejemplo
texto = response['message']['content']

# Generar voz calmada
generator = pipeline(texto, voice="em_alex", speed=0.7)

audio_chunks = []
for _, _, audio in generator:
    audio_chunks.append(audio)

# Concatenar todo el audio
audio_total = np.concatenate(audio_chunks)

# Guardar en archivo
sf.write("voz_kokoro.wav", audio_total, samplerate=24000)


In [41]:
Audio("voz_kokoro.wav")

In [4]:
collection_info = client.get_collection("buddhist_texts_mn")

print(collection_info)

status=<CollectionStatus.GREEN: 'green'> optimizer_status=<OptimizersStatusOneOf.OK: 'ok'> vectors_count=None indexed_vectors_count=0 points_count=8765 segments_count=8 config=CollectionConfig(params=CollectionParams(vectors=VectorParams(size=384, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None, datatype=None, multivector_config=None), shard_number=1, sharding_method=None, replication_factor=1, write_consistency_factor=1, read_fan_out_factor=None, on_disk_payload=True, sparse_vectors=None), hnsw_config=HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=False, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segment_number=0, max_segment_size=None, memmap_threshold=None, indexing_threshold=20000, flush_interval_sec=5, max_optimization_threads=None), wal_config=WalConfig(wal_capacity_mb=32, wal_segments_ahead=0), quantization_config=Non

In [3]:
EMBEDDINGS_DIR = "data/embeddings/tripitaka/mn"
TEXTS_DIR = "data/texts/tripitaka/mn"
OLLAMA_BASE_URL = "http://localhost:11434"
MODEL_NAME = "mistral"  # Change this to your specific model
EMBEDDING_MODEL = "all-MiniLM-L6-v2"
TOP_K = 3  # Number of most similar chunks to retrieve



In [ ]:
def load_embeddings_and_texts():
    """Load all embeddings and their corresponding texts"""
    embeddings = []
    texts = []
    metadata = []
    
    # Load embedding model for query encoding
    print("Loading embedding model...")
    embedding_model = SentenceTransformer(EMBEDDING_MODEL)
    
    # Iterate through all embedding files
    print("Loading embeddings and texts...")
    for embedding_file in Path(EMBEDDINGS_DIR).glob("*.npy"):
        # Load embedding
        embedding = np.load(embedding_file)
        
        # Load corresponding metadata
        metadata_file = embedding_file.with_suffix('.json')
        if metadata_file.exists():
            with open(metadata_file, 'r') as f:
                meta = json.load(f)
        else:
            meta = {"filename": embedding_file.stem, "chunk_id": 0}
        
        # Load corresponding text
        text_file = Path(TEXTS_DIR) / f"{meta['filename']}.txt"
        if text_file.exists():
            with open(text_file, 'r', encoding='utf-8') as f:
                text_content = f.read()
        else:
            text_content = f"Text from {meta['filename']}"
        
        embeddings.append(embedding)
        texts.append(text_content)
        metadata.append(meta)
    
    return np.array(embeddings), texts, metadata, embedding_model

def find_similar_chunks(query: str, embeddings, texts, metadata, embedding_model, top_k: int = TOP_K):
    """Find the most similar text chunks to the query"""
    # Encode the query
    query_embedding = embedding_model.encode([query])
    
    # Calculate cosine similarities
    similarities = np.dot(embeddings, query_embedding.T).flatten()
    
    # Get top-k indices
    top_indices = np.argsort(similarities)[::-1][:top_k]
    
    results = []
    for idx in top_indices:
        results.append((
            texts[idx],
            similarities[idx],
            metadata[idx]
        ))
    
    return results

def generate_response_with_ollama(query: str, context: str) -> str:
    """Generate a response using Ollama with the provided context"""
    url = f"{OLLAMA_BASE_URL}/api/generate"
    
    # Create a prompt that includes the context
    prompt = f"""Based on the following Buddhist text context, please answer the question.

Context:
{context}

Question: {query}

Please provide a thoughtful and accurate response based on the context provided:"""
    
    payload = {
        "model": MODEL_NAME,
        "prompt": prompt,
        "stream": False
    }
    
    try:
        response = requests.post(url, json=payload, timeout=30)
        response.raise_for_status()
        
        result = response.json()
        return result.get('response', 'No response generated')
    
    except requests.exceptions.RequestException as e:
        return f"Error communicating with Ollama: {str(e)}"
    except Exception as e:
        return f"Error generating response: {str(e)}"

def rag_query(query: str, embeddings, texts, metadata, embedding_model, top_k: int = TOP_K) -> Dict:
    """Complete RAG pipeline: retrieve relevant texts and generate response"""
    print(f"Query: {query}")
    print("-" * 50)
    
    # Step 1: Find similar chunks
    print("Searching for relevant texts...")
    similar_chunks = find_similar_chunks(query, embeddings, texts, metadata, embedding_model, top_k)
    
    # Step 2: Display retrieved chunks
    print(f"\nRetrieved {len(similar_chunks)} relevant chunks:")
    for i, (text, similarity, meta) in enumerate(similar_chunks, 1):
        print(f"\n--- Chunk {i} (Similarity: {similarity:.4f}) ---")
        print(f"Source: {meta.get('filename', 'Unknown')}")
        print(f"Text: {text[:200]}...")
    
    # Step 3: Combine context
    context = "\n\n".join([text for text, _, _ in similar_chunks])
    
    # Step 4: Generate response
    print("\nGenerating response with Ollama...")
    response = generate_response_with_ollama(query, context)
    
    return {
        "query": query,
        "retrieved_chunks": similar_chunks,
        "response": response,
        "context": context
    }

def interactive_rag():
    """Interactive interface for asking questions"""
    print("Buddhist Texts RAG System")
    print("Type 'quit' to exit")
    print("-" * 40)
    
    # Load data
    embeddings, texts, metadata, embedding_model = load_embeddings_and_texts()
    print(f"Loaded {len(embeddings)} embeddings")
    print(f"Embedding dimension: {embeddings.shape[1]}")
    
    while True:
        query = input("\nEnter your question: ").strip()
        
        if query.lower() in ['quit', 'exit', 'q']:
            print("Goodbye!")
            break
        
        if not query:
            continue
        
        try:
            result = rag_query(query, embeddings, texts, metadata, embedding_model)
            print("\n" + "="*60)
            print("RESPONSE:")
            print("="*60)
            print(result['response'])
            print("="*60)
        except Exception as e:
            print(f"Error: {str(e)}")

def test_rag():
    """Test the RAG system with a sample query"""
    # Load data
    embeddings, texts, metadata, embedding_model = load_embeddings_and_texts()
    print(f"Loaded {len(embeddings)} embeddings")
    print(f"Embedding dimension: {embeddings.shape[1]}")
    
    # Test query
    test_query = "What does the Buddha teach about mindfulness?"
    result = rag_query(test_query, embeddings, texts, metadata, embedding_model)
    
    print("\n" + "="*60)
    print("FINAL RESPONSE:")
    print("="*60)
    print(result['response'])

if __name__ == "__main__":
    import sys
    
    if len(sys.argv) > 1 and sys.argv[1] == "interactive":
        interactive_rag()
    else:
        test_rag() 